## This is to set your working path. You can work on your default path but ideally it is always good to have a separate folder and virtual environment for each project.

In [1]:
import os
os.chdir(r"C:\Users\abhis\Documents\Llama 2")

## Ensure to have requirements.txt file in the above path and execute the below command. Please use Ctrl+Enter to execute each cell

In [ ]:
pip install -r requirements.txt

## Importing the necessary libraries

In [2]:
from langchain import HuggingFacePipeline 
from langchain import PromptTemplate, LLMChain
from datetime import datetime
from transformers import pipeline
import os
import torch
import transformers
from transformers import AutoTokenizer, AutoModelForCausalLM 
from transformers import LlamaForCausalLM, LlamaTokenizer
from accelerate import init_empty_weights
from accelerate import infer_auto_device_map, init_empty_weights

In [3]:
print("Code Execution Start"+datetime.now().strftime("%H:%M:%S"))

model_path="./Static/Llama"

tokenizer = LlamaTokenizer.from_pretrained(model_path) 
model= LlamaForCausalLM.from_pretrained (model_path,device_map='auto',torch_dtype=torch.float32,
                                         use_auth_token=True,offload_folder="save_folder",local_files_only=True)
model.tie_weights()

if torch.backends.mps.is_available(): 
    mps_device = torch.device("mps")

#Please ensure these changes for GPU implementations
os.environ["SAFETENSORS FAST_GPU"]="1"
#torch_dtype=torch.bfloat16 is for GPU implementation only. For CPU, we have to make it 32
pipe = pipeline("text-generation",model=model,tokenizer=tokenizer,torch_dtype=torch.float32,device_map="auto",
                max_new_tokens = 40,do_sample=True,top_k=30,num_return_sequences=40,eos_token_id=tokenizer.eos_token_id)

You are using the default legacy behaviour of the <class 'transformers.models.llama.tokenization_llama.LlamaTokenizer'>. If you see this, DO NOT PANIC! This is expected, and simply means that the `legacy` (previous) behavior will be used so nothing changes for you. If you want to use the new behaviour, set `legacy=False`. This should only be set if you understand what it means, and thouroughly read the reason why this was added as explained in https://github.com/huggingface/transformers/pull/24565


Code Execution Start18:00:09


C:\Users\abhis\anaconda3\lib\site-packages\transformers\modeling_utils.py:2363: FutureWarning: The `use_auth_token` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [5]:
B_INST, E_INST = "[INST]", "[/INST]"
B_SYS, E_SYS = "<<SYS>>\n", "\n<</SYS>>\n\n" 
DEFAULT_SYSTEM_PROMPT = """\
You are a helpful, respectful and honest assistant. Always answer as helpfully as possible, while being safe.
If a question does not make any sense, or is not factually coherent, explain why instead of answering something"""

def get_prompt(instruction, new_system_prompt=DEFAULT_SYSTEM_PROMPT):
    SYSTEM_PROMPT = B_SYS + new_system_prompt + E_SYS
    prompt_template = B_INST + SYSTEM_PROMPT + instruction + E_INST
    return prompt_template


llm = HuggingFacePipeline(pipeline = pipe, model_kwargs = {'temperature': 0})
system_prompt = "You are an advanced assistant that excels at translation that answers query in one word. " 
instruction = "Translate the following word from English to french. :\n\n {text}" 
template = get_prompt(instruction, system_prompt)
print(template)
prompt = PromptTemplate(template=template, input_variables=["text"])
llm_chain = LLMChain(prompt=prompt, llm=llm)
text = "Dog"
print("Inferencing Started "+datetime.now().strftime("%H:%M:%S")) 
output = llm_chain.run(text)
print("OUTPUT>>>"+ output)
print("Inferencing Completed " +datetime.now().strftime("%H:%M:%S"))

[INST]<<SYS>>
You are an advanced assistant that excels at translation that answers query in one word. 
<</SYS>>

Translate the following word from English to french. :

 {text}[/INST]
Inferencing Started18:09:02
OUTPUT>>>  Chien
Inferencing Completed18:34:40
